# Used car sales data - exploring factors that influence price and demand

# Table of Contents

- [Introduction](#introduction)  
  - [Goal](#goal)
  - [Stages](#stages)
- [Stage 1: Data Overview](#1--data-overview)
  - [Concusions](#conclusions)
- [2. Data Preprocessing](#2.-data-preprocessing)
  - Converting data to correct datatypes
  - Treating missing values, duplicates and other errors
  - Treating outliers
  - Creating additional columns for future analysis

- [Stage 3: Hypotheses and Analysis](#stage-3-hypotheses-and-analysis)  
  - [Price by condition / brand / type](#price-by-condition--brand--type)  
  - [Price by model year / odometer](#price-by-model-year--odometer)  
  - [Price by days listed](#price-by-days-listed)
- Findings

# Introduction

## Goal

This is an exploratory analysis Notebook based on a dataset on used car sales: `../vehicles_us.csv`. The main goal is to determine which factors impact demand for a vehicle. The demand is measured: 
* in the price the car was sold for,
* in the number of days the car was listed before being sold.

## Stages

**Stage 1: Data Overview**

* Obtaining general information about the dataset

**Stage 2: Data Preprocessing**
* Converting data to correct datatypes
* Treating missing values, duplicates and other errors
* Creating additional columns for future analysis
* Setting up tools for treating outliers

**Stage 3: Analysis**
* 1
* 2
* 3

# 1. Data Overview

We start by importing the necessary modules and setting up the correct renderer for visual representations

In [1]:
import pandas as pd
import plotly_express as px
import plotly.io as pio
import plotly.graph_objects as go


pio.renderers.default = "notebook_connected"

Next, we import the dataset, and print the information needed for initial data overview:
* Information about the columns, missing values and data types
* First 10 rows of the dataset

In [2]:
df = pd.read_csv('../vehicles_us.csv')

# Display the basic information about the dataset
# - information about columns
# - first few rows of the dataset
df.info()
df.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   
5  14990      2014.0    chrysler 300  excellent        6.0  gas   57954.0   
6  12990      2015.0    toyota camry  excellent        4.0  gas   79212.0   
7  15990      2013.0     honda pilot  excellent        6.0  gas  109473.0   
8  11500      2012.0     kia sorento  excellent        4.0  gas  104174.0   
9   9200      2008.0     honda pilot  excellent        NaN  gas  147191.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28  
5    automatic   sedan       black     1.0  2018-06-20           15  
6    automatic   sedan       white     NaN  2018-12-27           73  
7    automatic     SUV       black     1.0  2019-01-07           68  
8    automatic     SUV         NaN     1.0  2018-07-16           19  
9    automatic     SUV        blue     1.0  2019-02-15           17

To get a better understanding of the data we will take a deeper look into some of the columns.


1. `condition` and `type`: we check the variety by printing lists of unique values in these columns.

In [3]:
print(df['condition'].unique())

print(df['type'].unique())

['good' 'like new' 'fair' 'excellent' 'salvage' 'new']
['SUV' 'pickup' 'sedan' 'truck' 'coupe' 'van' 'convertible' 'hatchback'
 'wagon' 'mini-van' 'other' 'offroad' 'bus']


2. To get an overview of `numerical columns`, we print basic statistics for them

In [4]:
# Checking basic info about columns with numerical data
numerical_columns = ['price', 'model_year', 'odometer', 'days_listed'] 
for column in numerical_columns:
    print(f'Column: {column}')
    print('Max:', df[column].max())
    print('Min:', df[column].min())
    print('Mean:', df[column].mean())
    print('Median:', df[column].median())
    print('\n')


Column: price
Max: 375000
Min: 1
Mean: 12132.464919941776
Median: 9000.0


Column: model_year
Max: 2019.0
Min: 1908.0
Mean: 2009.75046966977
Median: 2011.0


Column: odometer
Max: 990000.0
Min: 0.0
Mean: 115553.4617376756
Median: 113000.0


Column: days_listed
Max: 271
Min: 0
Mean: 39.55475982532751
Median: 33.0




Value `1` in the `price` column strikes as suspicious.

We can investigate further by counting how many times this value occurs

In [5]:
print('Price = 1:', df['price'].eq(1).sum(), 'cars')

Price = 1: 798 cars


These are likely either errors or spam. We will deal with these entries while preprocessing the data.
  
  
<br>

3. `days_listed` can still mean two different things:
* if the database contains information about a snapshot of car stock in time, `days_listed` means number of days the car was listed for before data capture
* if the database contains information about cars that have already been sold, `days_listed` means number of days the car was listed before being sold

    We can check this by comparing `days_listed` with `days_since_posted`. The new column `days_since_posted` is calculated as the difference between `date_posted` and the hypothetic date of the snapsot (assuming it's the latest of the dates in `date_posted`).

In [6]:
# Convert 'date_posted' to datetime format for handling date calculations
df['date_posted'] = pd.to_datetime(df['date_posted'])

# For every row - check the difference between latest date in 'date_posted' column and value of 'date_posted' for this row
# Append the result to a new column 'days_since_posted'
df['days_since_posted'] = (df['date_posted'].max() - df['date_posted']).dt.days

# For every row - check if 'days_since_posted' equals 'days_listed'
# Print count for True and False values
print(df['days_since_posted'].eq(df['days_listed']).value_counts())

False    51367
True       158
Name: count, dtype: int64


Most cars are not listed at the moment of database capture. For the purpose of this analysis, we can assume that these vehicles were sold.

## Conclusions

The database contains information about sales of different vehicles. All the information can be grouped into three categories (not in database order):
1. Car model's integral characteristic:
    * name of the model (including the name of the brand)
    * year of manufacture
    * type of the vehicle (sedan, coupe, bus, etc)
    * number of cylinders
    * type of transmission
    * type of the drivetrain (4WD or not) 
    * color of the vehicle
2. Specific vehicle's condition characteristics:
    * general condition description (from `salvage` to `new`)
    * odometer reading
3. Information about the sale:
    * Price the car was sold for
    * Number of days the car was listed before being sold
    * Date the listing was posted

After some preparation, we will be able to use this data to analyze which of the vehicle's characteristics impact the demand.


# 2. Data Preprocessing

## 2.1. Datatypes
We start with converting data to more fitting datatypes

In [7]:
# Convert 'model_year' and 'cylinders' to 'Int64' format
df['model_year'] = df['model_year'].astype('Int64')
df['cylinders'] = df['cylinders'].astype('Int64')

# 'date_posted' is already converted to 'datetime' format previously, so skipping that step here
# df['date_posted'] = pd.to_datetime(df['date_posted'])

# Safe-check - check if the conversion was successful
print(df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 14 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   price              51525 non-null  int64         
 1   model_year         47906 non-null  Int64         
 2   model              51525 non-null  object        
 3   condition          51525 non-null  object        
 4   cylinders          46265 non-null  Int64         
 5   fuel               51525 non-null  object        
 6   odometer           43633 non-null  float64       
 7   transmission       51525 non-null  object        
 8   type               51525 non-null  object        
 9   paint_color        42258 non-null  object        
 10  is_4wd             25572 non-null  float64       
 11  date_posted        51525 non-null  datetime64[ns]
 12  days_listed        51525 non-null  int64         
 13  days_since_posted  51525 non-null  int64         
dtypes: Int

## 2.2. Missing values

Next, we deal with missing values:
* `model_year` and `odometer` - can't be deduced from other columns. We will leave missing values as `NaN` to exclude them from analysis based on these columns
* `paint_color` - can't be deduced from other columns. We will fill missing values with `unknown` as this information is not crucial for the analysis
* `cylinders` - can be deduced from `model`. We will fill missing values with the most common value for a specific model
* `is_4wd` - contains only values `1.0` and `NaN`. We can assume that `1.0` means `4WD`, and `NaN` means `not 4WD`, or `AWD`, so we will replace the values accordingly       


In [8]:
# Fill missing values for 'cylinders' with the most common value in the column
df['cylinders'] = df['cylinders'].fillna(df['cylinders'].mode()[0])

# Fill missing values for 'paint_color' with 'unknown'
df['paint_color'] = df['paint_color'].fillna('unknown')

# Updating 'is_4wd' column:
df['is_4wd'] = df['is_4wd'].fillna('AWD')
df['is_4wd'] = df['is_4wd'].replace({1.0 : '4WD'})

# Safe-check - check if the missing values were filled correctly
print(df['cylinders'].unique())
print(df['paint_color'].unique())
print(df['is_4wd'].unique())

# Second safe-check - check number of remaining missing values and data types
print()
print(df.info())

<IntegerArray>
[6, 4, 8, 5, 10, 3, 12]
Length: 7, dtype: Int64
['unknown' 'white' 'red' 'black' 'blue' 'grey' 'silver' 'custom' 'orange'
 'yellow' 'brown' 'green' 'purple']
['4WD' 'AWD']

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 14 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   price              51525 non-null  int64         
 1   model_year         47906 non-null  Int64         
 2   model              51525 non-null  object        
 3   condition          51525 non-null  object        
 4   cylinders          51525 non-null  Int64         
 5   fuel               51525 non-null  object        
 6   odometer           43633 non-null  float64       
 7   transmission       51525 non-null  object        
 8   type               51525 non-null  object        
 9   paint_color        51525 non-null  object        
 10  is_4wd             51525 non-null  obj

All the datatypes are correct, and only `model_year` and `odometer` columns have `NaN` values

## 2.3. Duplicates

Next, we check database for duplicates

In [9]:
print(df.duplicated().sum())

0


Luckily, there are none.

## 2.4. Other probable errors

We previously noticed cars listed for $1, which seems too low to be true.

To be on the safe side, we will remove from analysis all vehicles with `price` below $300.

In [10]:
# Removing listings that have their price set below 300
df = df[(df['price'] > 300)]

# Safe-check - check how many rows were removed
print(df.info())

<class 'pandas.core.frame.DataFrame'>
Index: 50508 entries, 0 to 51524
Data columns (total 14 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   price              50508 non-null  int64         
 1   model_year         46954 non-null  Int64         
 2   model              50508 non-null  object        
 3   condition          50508 non-null  object        
 4   cylinders          50508 non-null  Int64         
 5   fuel               50508 non-null  object        
 6   odometer           42784 non-null  float64       
 7   transmission       50508 non-null  object        
 8   type               50508 non-null  object        
 9   paint_color        50508 non-null  object        
 10  is_4wd             50508 non-null  object        
 11  date_posted        50508 non-null  datetime64[ns]
 12  days_listed        50508 non-null  int64         
 13  days_since_posted  50508 non-null  int64         
dtypes: Int64(2)

## 2.5. Treating outliers

As the analysis will focus on demand for cars (`price` and `days_posted` columns), we will check if there any extreme outliers in these columns  that would impact the analysis. To do this, we create scatterplots for each.

In [11]:
# Scatterplot of 'price' distribution with median line

fig = px.scatter(df, y='price', title='Price Distribution')
fig.add_hline(y=df['price'].median(), line_dash='dash',
              annotation_text='Median', annotation_position='top right',
              line_color='green')

fig.show()


The scatterplot shows that there are significant outliers in the 'price' column. To mitigate this, we will set a threshold for the maximum price, using 99th percentile as a cutoff.

In [12]:
# Creating a 99th percentile threshold for removing outliers in the 'price' column
price_threshold = df['price'].quantile(0.99)
df_filtered = df[df['price'] < price_threshold]

fig = px.scatter(df_filtered, y='price', title='Price Distribution')
fig.add_hline(y=df_filtered['price'].median(), line_dash='dash',
              annotation_text='Median', annotation_position='top right',
              line_color='green')

fig.show()


In [13]:
# Scatterplot of 'days_listed' distribution with median line

fig = px.scatter(df, y='days_listed', title='days_listed Distribution')
fig.add_hline(y=df['days_listed'].median(), line_dash='dash',
              annotation_text='Median', annotation_position='top right',
              line_color='green')
fig.show()


There are no extreme outliers in the 'days_listed' column, so we can proceed with the analysis without filtering this column.

## 2.6. Creating `brand` column

For future comparisons, we can extract information about vehicle's brand from the `model` column and store it in a new `brand` column

In [14]:
# Creating 'brand' column, which contains the first word of the 'model' column
df['brand'] = df['model'].str.split().str[0]

# Safe-check - check if the 'brand' column was created correctly
print(df['brand'].unique())

['bmw' 'ford' 'hyundai' 'chrysler' 'toyota' 'honda' 'kia' 'chevrolet'
 'ram' 'gmc' 'jeep' 'nissan' 'subaru' 'dodge' 'mercedes-benz' 'acura'
 'cadillac' 'volkswagen' 'buick']


## Conclusions

We addressed several issues during preprocessing to improve data quality:

- Missing values in the `cylinders`, `paint_color`, and `is_4wd` columns were filled using appropriate strategies:

    - `cylinders` was filled with the most common value.

    - `paint_color` was replaced with `unknown`.

    - `is_4wd` was filled with `AWD`. `1.0` values were replaced with `4WD`.

- Invalid or extreme values in the `price` column were handled:

    - Listings priced under $300 were removed as unrealistic.

    - Outliers above the 99th percentile were excluded to reduce skew and improve visualization clarity.

- A new `brand` column was created by extracting the first word from the `model` field. This will help in grouping and analyzing vehicles by brand.

These steps improved the dataset`s consistency and prepared it for better analysis.

# Analysis

In [15]:
# Distribution of 'price' by 'condition'
# Using a custom order for 'condition' values - from worst to best

conditions_order = ['salvage', 'fair', 'good', 'excellent', 'like new', 'new']

fig = px.violin(
    df_filtered,
    y='price', 
    x='condition', 
    color='condition', 
    category_orders={'condition': conditions_order},
    title='Price Distribution by Condition')
fig.show()


In [16]:
# Distribution of 'price' by 'brand'
# Using a custom order for 'brand' values - from worst to best

brands_order = df_filtered.groupby('brand')['price'].median().sort_values().index.tolist()

fig = px.violin(
    df_filtered,
    y='price', 
    x='brand', 
    category_orders={'brand': brands_order},
    title='Price Distribution by Brand')
fig.show()


KeyError: 'brand'

In [ ]:
# Distribution of 'price' by 'type'
# Using a custom order for 'type' values - from worst to best

types_order = df_filtered.groupby('type')['price'].median().sort_values().index.tolist()

fig = px.box(
    df_filtered,
    y='price', 
    x='type', 
    category_orders={'type': types_order},
    title='Price Distribution by type')
fig.show()


In [ ]:
# Price distribution by 'odometer'
fig = px.scatter(
    df_filtered, 
    x='odometer', 
    y='price', title="Price distribution by Odometer")
fig.show()


In [ ]:
# Price distribution by 'model_year'
fig = px.scatter(
    df_filtered, 
    x='model_year', 
    y='price', title="Price distribution by Year")
fig.show()


In [ ]:
# Price distribution by 'days_listed'
fig = px.scatter(
    df_filtered, 
    x='days_listed', 
    y='price', 
    title="Price distribution by Year")
fig.show()
